# Bayesian Strategy Backtest Results
## True Portfolio Simulation (60% Core / 40% Satellites)

This notebook simulates actual portfolio values by:
- Loading selected ISINs for each month from backtest results
- Retrieving actual prices from the database
- Computing 60/40 allocation: 60% MSCI World (ACWI), 40% split among N satellites
- Comparing each N value against 100% ACWI baseline

In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from pathlib import Path
import warnings
import sqlite3

warnings.filterwarnings('ignore')

# Set up paths
results_dir = Path('./data/backtest_results')
db_path = Path('../maintenance/data/etf_database.db')

print("Available backtest results:")
for f in sorted(results_dir.glob('bayesian_backtest_N*.csv')):
    print(f"  {f.name}")

print(f"\nDatabase path: {db_path}")
print(f"Database exists: {db_path.exists()}")

Available backtest results:
  bayesian_backtest_N3.csv
  bayesian_backtest_N4.csv
  bayesian_backtest_N5.csv
  bayesian_backtest_N6.csv
  bayesian_backtest_N7.csv

Database path: ..\maintenance\data\etf_database.db
Database exists: True


In [2]:
# Load summary statistics from backtest (for reference)
summary_df = pd.read_csv(results_dir / 'bayesian_backtest_summary.csv')

print("\nBacktest Summary Statistics by N:")
print(summary_df[['n_satellites', 'annual_alpha', 'hit_rate', 'information_ratio', 'total_return']].to_string(index=False))


Backtest Summary Statistics by N:
 n_satellites  annual_alpha  hit_rate  information_ratio  total_return
            3      0.371740  0.925532           1.159887     16.063247
            4      0.352508  0.925532           1.179126     13.800283
            5      0.366926  0.914894           1.262064     15.539470
            6      0.348750  0.904255           1.169552     13.384953
            7      0.342878  0.904255           1.153197     12.759251


In [3]:
# Connect to database
conn = sqlite3.connect(db_path)

def get_price(isin, date):
    """Get price for an ISIN on a specific date (or closest date before)"""
    query = """
    SELECT price FROM prices 
    WHERE isin = ? AND date <= ? 
    ORDER BY date DESC 
    LIMIT 1
    """
    try:
        result = pd.read_sql_query(query, conn, params=(isin, date.strftime('%Y-%m-%d')))
        if len(result) > 0:
            return result['price'].iloc[0]
    except:
        pass
    return None

def get_prices_range(isin, date_from, date_to):
    """Get all prices for an ISIN within a date range"""
    query = """
    SELECT date, price FROM prices 
    WHERE isin = ? AND date >= ? AND date <= ? 
    ORDER BY date ASC
    """
    try:
        result = pd.read_sql_query(query, conn, params=(isin, date_from.strftime('%Y-%m-%d'), date_to.strftime('%Y-%m-%d')))
        return result
    except:
        return pd.DataFrame()

def simulate_portfolio_daily(backtest_df, n_satellites, core_isin='IE00B4L5Y983', initial_value=50000, monthly_dca=1000):
    """
    TRUE DAILY PORTFOLIO SIMULATION: Track daily prices with monthly rebalancing
    
    Includes Dollar Cost Averaging (DCA): Add monthly_dca amount at start of each month

    For each month:
    1. Add DCA contribution (except first month)
    2. Get selected ISINs for that month
    3. Rebalance to 60% core, 40% satellites
    4. Track daily portfolio value until end of month
    5. Repeat for next month
    """
    all_dates = []
    all_values = []
    daily_stats = []

    portfolio_value = initial_value
    months_processed = 0
    months_failed = 0

    for idx, row in backtest_df.iterrows():
        month_date = row['date']

        # Add DCA contribution at start of each month (except first month)
        if idx > 0:
            portfolio_value += monthly_dca

        # Determine end of month (next month's date or last date)
        if idx < len(backtest_df) - 1:
            end_date = backtest_df.iloc[idx + 1]['date']
        else:
            # Use end of month approximation
            end_date = (month_date + pd.DateOffset(months=1)).replace(day=1) - pd.DateOffset(days=1)

        # Get prices at START of month (for buying)
        core_price_start = get_price(core_isin, month_date)
        if core_price_start is None:
            months_failed += 1
            continue

        # Parse selected ISINs
        selected_isins = [isin.strip() for isin in str(row['selected_isins']).split(',')]

        # Get satellite prices at start of month
        sat_prices_start = {}
        found_all = True
        for isin in selected_isins:
            price = get_price(isin, month_date)
            if price is not None:
                sat_prices_start[isin] = price
            else:
                found_all = False
                break

        if not found_all or len(sat_prices_start) != len(selected_isins):
            months_failed += 1
            continue

        # REBALANCING: Allocate 60% core, 40% satellites
        core_allocation = portfolio_value * 0.60
        satellite_allocation = portfolio_value * 0.40
        allocation_per_satellite = satellite_allocation / n_satellites

        # BUY positions at start of month
        core_units = core_allocation / core_price_start
        satellite_holdings = {}
        for isin in selected_isins:
            satellite_holdings[isin] = allocation_per_satellite / sat_prices_start[isin]

        # Get daily prices for this month
        core_prices_df = get_prices_range(core_isin, month_date, end_date)
        if len(core_prices_df) == 0:
            months_failed += 1
            continue

        # Get all satellite prices - FIX: convert dates to strings for dict lookup
        all_sat_prices = {}
        missing_satellite = False
        for isin in selected_isins:
            sat_df = get_prices_range(isin, month_date, end_date)
            if len(sat_df) > 0:
                # Store as {date_string: price} to avoid type mismatch
                all_sat_prices[isin] = dict(zip(sat_df['date'].astype(str), sat_df['price']))
            else:
                missing_satellite = True
                break

        if missing_satellite:
            months_failed += 1
            continue

        # Track daily values for this month
        month_days = 0
        for _, core_row in core_prices_df.iterrows():
            date_str = str(core_row['date'])  # Keep as string for dict lookup
            current_date = pd.to_datetime(date_str)  # Convert to datetime for output
            current_core_price = core_row['price']

            # Get satellite prices for this date
            core_value = core_units * current_core_price
            satellite_value = 0
            found_all_sat = True

            for isin, units in satellite_holdings.items():
                if date_str in all_sat_prices[isin]:
                    sat_price = all_sat_prices[isin][date_str]
                    satellite_value += units * sat_price
                else:
                    found_all_sat = False
                    break

            if found_all_sat:
                # All satellite prices found for this date
                daily_portfolio_value = core_value + satellite_value

                all_dates.append(current_date)
                all_values.append(daily_portfolio_value)

                daily_stats.append({
                    'date': current_date,
                    'portfolio_value': daily_portfolio_value,
                    'core_value': core_value,
                    'satellite_value': satellite_value,
                    'month': month_date
                })

                portfolio_value = daily_portfolio_value
                month_days += 1

        if month_days > 0:
            months_processed += 1

    return all_dates, all_values, daily_stats, months_processed, months_failed

# Core ISIN
CORE_ISIN = 'IE00B4L5Y983'

# DCA Parameters
INITIAL_INVESTMENT = 50000
MONTHLY_DCA = 1000

# Load and simulate all N values
all_results = {}
backtest_dfs = {}
baseline_dates = None
baseline_values = None
baseline_daily_stats = None

print("Running DAILY portfolio simulation (60% core / 40% satellites)")
print(f"Initial Investment: EUR {INITIAL_INVESTMENT:,}")
print(f"Monthly DCA: EUR {MONTHLY_DCA:,}")
print("=" * 70)

for n in range(3, 8):
    file_path = results_dir / f'bayesian_backtest_N{n}.csv'
    if file_path.exists():
        df = pd.read_csv(file_path)
        df['date'] = pd.to_datetime(df['date'])
        df = df.sort_values('date').reset_index(drop=True)
        
        # Store for alpha plotting
        backtest_dfs[f'N={n}'] = df
        
        # Simulate strategy with DCA
        dates, values, daily_stats, months_ok, months_fail = simulate_portfolio_daily(
            df, n, CORE_ISIN, 
            initial_value=INITIAL_INVESTMENT, 
            monthly_dca=MONTHLY_DCA
        )
        
        # Simulate baseline (100% core ACWI) with same DCA - only once
        if baseline_dates is None:
            baseline_dates = []
            baseline_values = []
            baseline_daily_stats = []
            
            baseline_portfolio_value = INITIAL_INVESTMENT
            
            for idx, brow in df.iterrows():
                month_date = brow['date']
                
                # Add DCA at start of each month (except first)
                if idx > 0:
                    baseline_portfolio_value += MONTHLY_DCA
                
                # Determine end of month
                if idx < len(df) - 1:
                    end_date = df.iloc[idx + 1]['date']
                else:
                    end_date = (month_date + pd.DateOffset(months=1)).replace(day=1) - pd.DateOffset(days=1)
                
                # Get prices
                core_price_start = get_price(CORE_ISIN, month_date)
                if core_price_start is None:
                    continue
                
                # Buy ACWI at start of month
                baseline_units = baseline_portfolio_value / core_price_start
                
                # Track daily values for this month
                baseline_prices_df = get_prices_range(CORE_ISIN, month_date, end_date)
                if len(baseline_prices_df) == 0:
                    continue
                
                for _, base_row in baseline_prices_df.iterrows():
                    date = pd.to_datetime(base_row['date'])
                    price = base_row['price']
                    baseline_value = baseline_units * price
                    
                    baseline_dates.append(date)
                    baseline_values.append(baseline_value)
                    baseline_daily_stats.append({
                        'date': date,
                        'portfolio_value': baseline_value
                    })
                
                baseline_portfolio_value = baseline_value
        
        if len(dates) > 0 and len(values) > 0:
            all_results[f'N={n}'] = {'dates': dates, 'values': values, 'daily_stats': daily_stats}
            final_value = values[-1] if values else INITIAL_INVESTMENT
            baseline_final = baseline_values[-1] if baseline_values else INITIAL_INVESTMENT
            gain = final_value - INITIAL_INVESTMENT
            baseline_gain = baseline_final - INITIAL_INVESTMENT
            alpha = final_value - baseline_final
            
            print(f"  N={n}: {len(values):5d} days | {months_ok:2d} months OK")
            print(f"        Final: EUR {final_value:8,.0f} (+EUR {gain:7,.0f}) | "
                  f"vs Baseline: EUR {baseline_final:8,.0f} (+EUR {baseline_gain:7,.0f}) | "
                  f"Alpha: EUR {alpha:+8,.0f}")
        else:
            print(f"  N={n}: FAILED - {months_ok} months OK, {months_fail} failed to process")

conn.close()
print("=" * 70)
print(f"{len(all_results)} strategies simulated successfully")

Running DAILY portfolio simulation (60% core / 40% satellites)
Initial Investment: EUR 50,000
Monthly DCA: EUR 1,000
  N=3:  2926 days | 94 months OK
        Final: EUR  715,994 (+EUR 665,994) | vs Baseline: EUR  282,054 (+EUR 232,054) | Alpha: EUR +433,940
  N=4:  2926 days | 94 months OK
        Final: EUR  683,402 (+EUR 633,402) | vs Baseline: EUR  282,054 (+EUR 232,054) | Alpha: EUR +401,348
  N=5:  2926 days | 94 months OK
        Final: EUR  710,110 (+EUR 660,110) | vs Baseline: EUR  282,054 (+EUR 232,054) | Alpha: EUR +428,056
  N=6:  2926 days | 94 months OK
        Final: EUR  679,411 (+EUR 629,411) | vs Baseline: EUR  282,054 (+EUR 232,054) | Alpha: EUR +397,357
  N=7:  2926 days | 94 months OK
        Final: EUR  671,030 (+EUR 621,030) | vs Baseline: EUR  282,054 (+EUR 232,054) | Alpha: EUR +388,976
5 strategies simulated successfully


In [4]:
# Calculate cumulative contributions line
# This shows how much you've invested over time (initial + monthly DCA)
contribution_dates = []
contribution_values = []

# Get dates from first strategy to align with simulation
if all_results:
    first_strategy_data = list(all_results.values())[0]
    strategy_dates = first_strategy_data['dates']
    
    # For each date, calculate cumulative contributions
    # Initial investment: 50,000 at first date
    # Then add 1,000 at the start of each month after first month
    
    contribution_dates.append(strategy_dates[0])
    contribution_values.append(INITIAL_INVESTMENT)
    
    current_month = None
    for date in strategy_dates[1:]:
        # Check if we've entered a new month
        month_key = (date.year, date.month)
        
        if current_month is None:
            current_month = (strategy_dates[0].year, strategy_dates[0].month)
        
        if month_key != current_month:
            # New month detected - add DCA contribution
            # Find the first day of this new month
            new_contribution = contribution_values[-1] + MONTHLY_DCA
            contribution_dates.append(date)
            contribution_values.append(new_contribution)
            current_month = month_key
        
        # Continue with same contribution value for rest of month
        contribution_dates.append(date)
        contribution_values.append(contribution_values[-1])

# Calculate cumulative transaction costs for each N (for separate cost plot)
# Worst case: Core ETF = EUR 1 per trade, Satellites = EUR 3 per trade
# Each rebalancing involves: sell old positions + buy new positions
# Month 1: Buy core (1) + buy N satellites (3*N) = 1 + 3*N
# Month 2+: Sell core (1) + sell N satellites (3*N) + Buy core (1) + buy N satellites (3*N) = 2 + 6*N

transaction_costs_by_n = {}

if all_results:
    for label in all_results.keys():
        # Extract N from label (e.g., "N=3" -> 3)
        n_value = int(label.split('=')[1])
        
        transaction_dates = []
        transaction_costs = []
        cumulative_cost = 0
        current_month = None
        
        for date in strategy_dates:
            month_key = (date.year, date.month)
            
            # Check if we've entered a new month
            if current_month is None:
                current_month = month_key
                # Month 1: cost = 1 + 3*N (buy core + buy N satellites)
                cost_this_month = 1 + (3 * n_value)
            elif month_key != current_month:
                # Month 2+: cost = 2 + 6*N (sell old + buy new for both core and satellites)
                cost_this_month = 2 + (6 * n_value)
                current_month = month_key
            else:
                cost_this_month = 0  # Same month, no new cost yet
            
            cumulative_cost += cost_this_month
            transaction_dates.append(date)
            transaction_costs.append(cumulative_cost)
        
        transaction_costs_by_n[label] = {
            'dates': transaction_dates,
            'costs': transaction_costs,
            'n_value': n_value
        }
    
    # Now calculate opportunity costs for each N (COMPOUNDING from cost date to TODAY)
    for label in all_results.keys():
        strategy_values = np.array(all_results[label]['values'])
        strategy_dates_arr = np.array(all_results[label]['dates'])
        cost_data = transaction_costs_by_n[label]
        
        # Track when each monthly cost was incurred and the amount
        cost_increase_dates = []
        monthly_cost_amounts = []
        
        for i in range(len(cost_data['costs'])):
            if i == 0:
                # First cost (month 1)
                cost_increase_dates.append(cost_data['dates'][i])
                monthly_cost_amounts.append(cost_data['costs'][i])
            elif cost_data['costs'][i] > cost_data['costs'][i-1]:
                # Cost increased (new month)
                cost_increase_dates.append(cost_data['dates'][i])
                monthly_cost_amounts.append(cost_data['costs'][i] - cost_data['costs'][i-1])
        
        # Calculate opportunity cost for each date
        # COMPOUNDING: For each date, each paid cost grows from when paid to TODAY (not to end)
        opportunity_cost_values = []
        
        for current_idx in range(len(strategy_values)):
            current_date = strategy_dates_arr[current_idx]
            current_value = strategy_values[current_idx]
            
            # Sum up opportunity cost of all costs paid up to current date
            # Each cost compounds from when it was paid to today
            opp_cost = 0
            for cost_date, cost_amount in zip(cost_increase_dates, monthly_cost_amounts):
                if cost_date <= current_date:
                    # This cost was paid by now
                    # Find the portfolio value at the date this cost was paid
                    cost_date_idx = np.searchsorted(strategy_dates_arr, cost_date)
                    portfolio_value_at_cost = strategy_values[cost_date_idx]
                    
                    # Growth from cost date to TODAY (not to end)
                    # This creates the compounding effect
                    growth = current_value / portfolio_value_at_cost if portfolio_value_at_cost > 0 else 1
                    
                    # Add this cost's opportunity value at today's date
                    opp_cost += cost_amount * growth
            
            opportunity_cost_values.append(opp_cost)
        
        cost_data['opportunity_costs'] = opportunity_cost_values

# Create interactive plot with all N values - TRUE SIMULATION
fig = go.Figure()

# Color palette for strategies
colors = {
    'N=3': '#00D9FF',  # Cyan
    'N=4': '#FFD700',  # Gold
    'N=5': '#00FF41',  # Green
    'N=6': '#FF6B6B',  # Red
    'N=7': '#9D4EDD',  # Purple
    'Baseline': '#CCCCCC', # Gray
    'Contributions': '#FF9500',  # Orange
}

# Add baseline (100% core)
if baseline_dates is not None and baseline_values is not None:
    fig.add_trace(go.Scatter(
        x=baseline_dates,
        y=baseline_values,
        mode='lines',
        name='Baseline (100% ACWI)',
        line=dict(color=colors['Baseline'], width=3, dash='dash'),
        hovertemplate='<b>Baseline (100% ACWI)</b><br>Date: %{x|%Y-%m-%d}<br>Portfolio Value: EUR %{y:,.0f}<extra></extra>'
    ))

# Add contributions line
if contribution_dates:
    fig.add_trace(go.Scatter(
        x=contribution_dates,
        y=contribution_values,
        mode='lines',
        name='Your Contributions (50k + 1k/month)',
        line=dict(color=colors['Contributions'], width=2.5, dash='dot'),
        hovertemplate='<b>Contributions</b><br>Date: %{x|%Y-%m-%d}<br>Total Invested: EUR %{y:,.0f}<extra></extra>'
    ))

# Add all N values (solid lines)
for label in sorted(all_results.keys()):
    data = all_results[label]
    fig.add_trace(go.Scatter(
        x=data['dates'],
        y=data['values'],
        mode='lines',
        name=label,
        line=dict(color=colors.get(label, '#FFFFFF'), width=2.5),
        hovertemplate=f'<b>{label}</b><br>Date: %{{x|%Y-%m-%d}}<br>Portfolio Value: EUR %{{y:,.0f}}<extra></extra>'
    ))

# Update layout for dark theme
fig.update_layout(
    title={
        'text': 'Bayesian Strategy Portfolio Simulation (60% Core / 40% Satellites) with DCA',
        'x': 0.5,
        'xanchor': 'center',
        'font': {'size': 20, 'color': '#FFFFFF'}
    },
    xaxis=dict(
        title='Date',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        zeroline=False,
        color='#FFFFFF'
    ),
    yaxis=dict(
        title='Portfolio Value (EUR)',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        color='#FFFFFF'
    ),
    plot_bgcolor='#1a1a1a',
    paper_bgcolor='#0d0d0d',
    font=dict(color='#FFFFFF', size=12),
    hovermode='x unified',
    legend=dict(
        bgcolor='rgba(0,0,0,0.5)',
        bordercolor='#FFFFFF',
        borderwidth=1,
        font=dict(color='#FFFFFF'),
        yanchor='top',
        y=0.99,
        xanchor='left',
        x=0.01
    ),
    height=700,
    width=1400,
    margin=dict(l=80, r=80, t=100, b=80)
)

fig.show()

In [5]:
# Plot transaction costs + opportunity costs (calculated in cell above)
fig_costs = go.Figure()

# Color palette
colors = {
    'N=3': '#00D9FF',  # Cyan
    'N=4': '#FFD700',  # Gold
    'N=5': '#00FF41',  # Green
    'N=6': '#FF6B6B',  # Red
    'N=7': '#9D4EDD',  # Purple
}

# Add cumulative transaction costs for each N (solid lines)
for label in sorted(transaction_costs_by_n.keys()):
    cost_data = transaction_costs_by_n[label]
    fig_costs.add_trace(go.Scatter(
        x=cost_data['dates'],
        y=cost_data['costs'],
        mode='lines',
        name=f'{label} - Actual Costs',
        line=dict(color=colors.get(label, '#FFFFFF'), width=2.5),
        hovertemplate=f'<b>{label} Actual Costs</b><br>Date: %{{x|%Y-%m-%d}}<br>EUR %{{y:,.0f}}<extra></extra>'
    ))

# Add opportunity costs for each N (dashed lines)
for label in sorted(transaction_costs_by_n.keys()):
    cost_data = transaction_costs_by_n[label]
    fig_costs.add_trace(go.Scatter(
        x=cost_data['dates'],
        y=cost_data['opportunity_costs'],
        mode='lines',
        name=f'{label} - Opportunity Cost (if invested)',
        line=dict(color=colors.get(label, '#FFFFFF'), width=2.5, dash='dash'),
        hovertemplate=f'<b>{label} Opportunity Cost</b><br>Date: %{{x|%Y-%m-%d}}<br>EUR %{{y:,.0f}}<extra></extra>'
    ))

# Update layout for dark theme
fig_costs.update_layout(
    title={
        'text': 'Transaction Costs vs Opportunity Cost (Core: 1€, Satellites: 3€)',
        'x': 0.5,
        'xanchor': 'center',
        'font': {'size': 20, 'color': '#FFFFFF'}
    },
    xaxis=dict(
        title='Date',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        zeroline=False,
        color='#FFFFFF'
    ),
    yaxis=dict(
        title='Costs (EUR)',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        color='#FFFFFF'
    ),
    plot_bgcolor='#1a1a1a',
    paper_bgcolor='#0d0d0d',
    font=dict(color='#FFFFFF', size=12),
    hovermode='x unified',
    legend=dict(
        bgcolor='rgba(0,0,0,0.5)',
        bordercolor='#FFFFFF',
        borderwidth=1,
        font=dict(color='#FFFFFF'),
        yanchor='top',
        y=0.99,
        xanchor='left',
        x=0.01
    ),
    height=600,
    width=1400,
    margin=dict(l=80, r=80, t=100, b=80)
)

fig_costs.show()

print("\nTransaction Cost vs Opportunity Cost Summary:")
print("=" * 70)
for label in sorted(transaction_costs_by_n.keys()):
    cost_data = transaction_costs_by_n[label]
    n_val = cost_data['n_value']
    actual_cost = cost_data['costs'][-1]
    opportunity_cost = cost_data['opportunity_costs'][-1]
    
    print(f"\n{label}:")
    print(f"  Actual transaction costs spent: EUR {actual_cost:,.0f}")
    print(f"  If invested in {label} portfolio: EUR {opportunity_cost:,.0f}")
    print(f"  Opportunity cost (foregone gains): EUR {opportunity_cost - actual_cost:,.0f}")
print()


Transaction Cost vs Opportunity Cost Summary:

N=3:
  Actual transaction costs spent: EUR 1,870
  If invested in N=3 portfolio: EUR 8,956
  Opportunity cost (foregone gains): EUR 7,086

N=4:
  Actual transaction costs spent: EUR 2,431
  If invested in N=4 portfolio: EUR 11,245
  Opportunity cost (foregone gains): EUR 8,814

N=5:
  Actual transaction costs spent: EUR 2,992
  If invested in N=5 portfolio: EUR 14,207
  Opportunity cost (foregone gains): EUR 11,215

N=6:
  Actual transaction costs spent: EUR 3,553
  If invested in N=6 portfolio: EUR 16,419
  Opportunity cost (foregone gains): EUR 12,866

N=7:
  Actual transaction costs spent: EUR 4,114
  If invested in N=7 portfolio: EUR 18,890
  Opportunity cost (foregone gains): EUR 14,776



In [6]:
# Create net portfolio plot (after subtracting opportunity costs)
# This shows the REAL portfolio value after accounting for transaction cost drag
fig_net = go.Figure()

# Color palette for strategies
colors = {
    'N=3': '#00D9FF',  # Cyan
    'N=4': '#FFD700',  # Gold
    'N=5': '#00FF41',  # Green
    'N=6': '#FF6B6B',  # Red
    'N=7': '#9D4EDD',  # Purple
    'Baseline': '#CCCCCC', # Gray
    'Contributions': '#FF9500',  # Orange
}

# Add baseline (100% core) - no transaction costs
if baseline_dates is not None and baseline_values is not None:
    fig_net.add_trace(go.Scatter(
        x=baseline_dates,
        y=baseline_values,
        mode='lines',
        name='Baseline (100% ACWI)',
        line=dict(color=colors['Baseline'], width=3, dash='dash'),
        hovertemplate='<b>Baseline (100% ACWI)</b><br>Date: %{x|%Y-%m-%d}<br>Net Portfolio Value: EUR %{y:,.0f}<extra></extra>'
    ))

# Add contributions line
if contribution_dates:
    fig_net.add_trace(go.Scatter(
        x=contribution_dates,
        y=contribution_values,
        mode='lines',
        name='Your Contributions (50k + 1k/month)',
        line=dict(color=colors['Contributions'], width=2.5, dash='dot'),
        hovertemplate='<b>Contributions</b><br>Date: %{x|%Y-%m-%d}<br>Total Invested: EUR %{y:,.0f}<extra></extra>'
    ))

# Add all N values with costs subtracted (net portfolio value)
for label in sorted(all_results.keys()):
    data = all_results[label]
    opportunity_costs = transaction_costs_by_n[label]['opportunity_costs']
    
    # Net value = Gross portfolio value - Opportunity cost
    net_values = np.array(data['values']) - np.array(opportunity_costs)
    
    fig_net.add_trace(go.Scatter(
        x=data['dates'],
        y=net_values,
        mode='lines',
        name=f'{label} (after costs)',
        line=dict(color=colors.get(label, '#FFFFFF'), width=2.5),
        hovertemplate=f'<b>{label} Net Value</b><br>Date: %{{x|%Y-%m-%d}}<br>Portfolio Value: EUR %{{y:,.0f}}<extra></extra>'
    ))

# Update layout for dark theme
fig_net.update_layout(
    title={
        'text': 'Bayesian Strategy Portfolio Simulation - NET VALUE (After Transaction Cost Drag)',
        'x': 0.5,
        'xanchor': 'center',
        'font': {'size': 20, 'color': '#FFFFFF'}
    },
    xaxis=dict(
        title='Date',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        zeroline=False,
        color='#FFFFFF'
    ),
    yaxis=dict(
        title='Net Portfolio Value (EUR)',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        color='#FFFFFF'
    ),
    plot_bgcolor='#1a1a1a',
    paper_bgcolor='#0d0d0d',
    font=dict(color='#FFFFFF', size=12),
    hovermode='x unified',
    legend=dict(
        bgcolor='rgba(0,0,0,0.5)',
        bordercolor='#FFFFFF',
        borderwidth=1,
        font=dict(color='#FFFFFF'),
        yanchor='top',
        y=0.99,
        xanchor='left',
        x=0.01
    ),
    height=700,
    width=1400,
    margin=dict(l=80, r=80, t=100, b=80)
)

fig_net.show()

print("\nNet Portfolio Value Summary (After Transaction Costs):")
print("=" * 80)
print(f"{'Strategy':<15} {'Gross Final':<18} {'Opp. Cost':<18} {'Net Final':<18} {'vs Baseline':<15}")
print("-" * 80)

baseline_final = baseline_values[-1] if baseline_values else 0

for label in sorted(all_results.keys()):
    data = all_results[label]
    opportunity_costs = transaction_costs_by_n[label]['opportunity_costs']
    
    gross_final = data['values'][-1]
    opp_cost_final = opportunity_costs[-1]
    net_final = gross_final - opp_cost_final
    vs_baseline = net_final - baseline_final
    
    print(f"{label:<15} EUR {gross_final:>13,.0f}  EUR {opp_cost_final:>13,.0f}  EUR {net_final:>13,.0f}  EUR {vs_baseline:>+10,.0f}")

print("-" * 80)
print(f"{'Baseline':<15} EUR {baseline_final:>13,.0f}  EUR {'0':>13}  EUR {baseline_final:>13,.0f}  EUR {'0':>10}")
print()


Net Portfolio Value Summary (After Transaction Costs):
Strategy        Gross Final        Opp. Cost          Net Final          vs Baseline    
--------------------------------------------------------------------------------
N=3             EUR       715,994  EUR         8,956  EUR       707,038  EUR   +424,984
N=4             EUR       683,402  EUR        11,245  EUR       672,158  EUR   +390,104
N=5             EUR       710,110  EUR        14,207  EUR       695,903  EUR   +413,849
N=6             EUR       679,411  EUR        16,419  EUR       662,992  EUR   +380,938
N=7             EUR       671,030  EUR        18,890  EUR       652,140  EUR   +370,086
--------------------------------------------------------------------------------
Baseline        EUR       282,054  EUR             0  EUR       282,054  EUR          0



In [7]:
# Create a dedicated plot for drawdowns only
fig_dd = go.Figure()

# Color palette (same as before)
colors = {
    'N=3': '#00D9FF',  # Cyan
    'N=4': '#FFD700',  # Gold
    'N=5': '#00FF41',  # Green
    'N=6': '#FF6B6B',  # Red
    'N=7': '#9D4EDD',  # Purple
    'Baseline': '#CCCCCC', # Gray
}

# Calculate and plot drawdown for baseline
if baseline_dates is not None and baseline_values is not None:
    baseline_arr = np.array(baseline_values)
    running_max = np.maximum.accumulate(baseline_arr)
    drawdown = ((baseline_arr - running_max) / running_max) * 100  # As percentage
    
    fig_dd.add_trace(go.Scatter(
        x=baseline_dates,
        y=drawdown,
        mode='lines',
        name='Baseline (100% ACWI)',
        line=dict(color=colors['Baseline'], width=3, dash='dash'),
        fill='tozeroy',
        fillcolor='rgba(204, 204, 204, 0.1)',
        hovertemplate='<b>Baseline (100% ACWI)</b><br>Date: %{x|%Y-%m-%d}<br>Drawdown: %{y:.2f}%<extra></extra>'
    ))

# Calculate and plot drawdown for each strategy
for label in sorted(all_results.keys()):
    data = all_results[label]
    values_arr = np.array(data['values'])
    running_max = np.maximum.accumulate(values_arr)
    drawdown = ((values_arr - running_max) / running_max) * 100  # As percentage
    
    fig_dd.add_trace(go.Scatter(
        x=data['dates'],
        y=drawdown,
        mode='lines',
        name=label,
        line=dict(color=colors.get(label, '#FFFFFF'), width=2.5),
        hovertemplate=f'<b>{label}</b><br>Date: %{{x|%Y-%m-%d}}<br>Drawdown: %{{y:.2f}}%<extra></extra>'
    ))

# Add zero line to show no drawdown
if all_results:
    first_dates = list(all_results.values())[0]['dates']
    fig_dd.add_trace(go.Scatter(
        x=[first_dates[0], first_dates[-1]],
        y=[0, 0],
        mode='lines',
        name='No Drawdown',
        line=dict(color='#666666', width=1, dash='dash'),
        hoverinfo='skip'
    ))

# Update layout for dark theme
fig_dd.update_layout(
    title={
        'text': 'Portfolio Drawdown Analysis (Peak-to-Trough Decline)',
        'x': 0.5,
        'xanchor': 'center',
        'font': {'size': 20, 'color': '#FFFFFF'}
    },
    xaxis=dict(
        title='Date',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        zeroline=False,
        color='#FFFFFF'
    ),
    yaxis=dict(
        title='Drawdown (%)',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        color='#FFFFFF',
        zeroline=True,
        zerolinecolor='#555555',
        zerolinewidth=2
    ),
    plot_bgcolor='#1a1a1a',
    paper_bgcolor='#0d0d0d',
    font=dict(color='#FFFFFF', size=12),
    hovermode='x unified',
    legend=dict(
        bgcolor='rgba(0,0,0,0.5)',
        bordercolor='#FFFFFF',
        borderwidth=1,
        font=dict(color='#FFFFFF'),
        yanchor='bottom',
        y=0.01,
        xanchor='left',
        x=0.01
    ),
    height=700,
    width=1400,
    margin=dict(l=80, r=80, t=100, b=80)
)

fig_dd.show()

In [8]:
# Compute daily statistics
print("\n" + "="*70)
print("DAILY PORTFOLIO STATISTICS")
print("="*70)

for label in sorted(all_results.keys()):
    data = all_results[label]
    values = np.array(data['values'])
    dates = data['dates']
    
    # Compute returns
    daily_returns = np.diff(values) / values[:-1]
    
    # Compute statistics
    total_return = (values[-1] / values[0]) - 1
    annual_return = (1 + total_return) ** (252 / len(values)) - 1
    daily_vol = np.std(daily_returns)
    annual_vol = daily_vol * np.sqrt(252)
    sharpe = annual_return / annual_vol if annual_vol > 0 else 0
    
    # Drawdown
    cummax = np.maximum.accumulate(values)
    drawdown = (values - cummax) / cummax
    max_drawdown = np.min(drawdown)
    
    # Win rate
    positive_days = np.sum(daily_returns > 0) / len(daily_returns)
    
    print(f"\n{label}:")
    print(f"  Days: {len(values)}")
    print(f"  Final Value: {values[-1]:.2f}")
    print(f"  Total Return: {total_return:.2%}")
    print(f"  Annual Return: {annual_return:.2%}")
    print(f"  Annual Volatility: {annual_vol:.2%}")
    print(f"  Sharpe Ratio: {sharpe:.3f}")
    print(f"  Max Drawdown: {max_drawdown:.2%}")
    print(f"  Win Rate: {positive_days:.1%}")

# Baseline stats
if baseline_values:
    baseline_values_arr = np.array(baseline_values)
    baseline_returns = np.diff(baseline_values_arr) / baseline_values_arr[:-1]
    
    total_return = (baseline_values_arr[-1] / baseline_values_arr[0]) - 1
    annual_return = (1 + total_return) ** (252 / len(baseline_values_arr)) - 1
    daily_vol = np.std(baseline_returns)
    annual_vol = daily_vol * np.sqrt(252)
    sharpe = annual_return / annual_vol if annual_vol > 0 else 0
    
    cummax = np.maximum.accumulate(baseline_values_arr)
    drawdown = (baseline_values_arr - cummax) / cummax
    max_drawdown = np.min(drawdown)
    
    positive_days = np.sum(baseline_returns > 0) / len(baseline_returns)
    
    print(f"\nBaseline (100% ACWI):")
    print(f"  Days: {len(baseline_values_arr)}")
    print(f"  Final Value: {baseline_values_arr[-1]:.2f}")
    print(f"  Total Return: {total_return:.2%}")
    print(f"  Annual Return: {annual_return:.2%}")
    print(f"  Annual Volatility: {annual_vol:.2%}")
    print(f"  Sharpe Ratio: {sharpe:.3f}")
    print(f"  Max Drawdown: {max_drawdown:.2%}")
    print(f"  Win Rate: {positive_days:.1%}")

print("="*70)


DAILY PORTFOLIO STATISTICS

N=3:
  Days: 2926
  Final Value: 715994.10
  Total Return: 1331.99%
  Annual Return: 25.76%
  Annual Volatility: 12.45%
  Sharpe Ratio: 2.070
  Max Drawdown: -25.66%
  Win Rate: 42.9%

N=4:
  Days: 2926
  Final Value: 683402.47
  Total Return: 1266.80%
  Annual Return: 25.26%
  Annual Volatility: 12.38%
  Sharpe Ratio: 2.040
  Max Drawdown: -25.77%
  Win Rate: 42.9%

N=5:
  Days: 2926
  Final Value: 710109.65
  Total Return: 1320.22%
  Annual Return: 25.67%
  Annual Volatility: 12.17%
  Sharpe Ratio: 2.110
  Max Drawdown: -25.65%
  Win Rate: 42.6%

N=6:
  Days: 2926
  Final Value: 679411.42
  Total Return: 1258.82%
  Annual Return: 25.20%
  Annual Volatility: 12.10%
  Sharpe Ratio: 2.083
  Max Drawdown: -25.75%
  Win Rate: 42.5%

N=7:
  Days: 2926
  Final Value: 671030.03
  Total Return: 1242.06%
  Annual Return: 25.06%
  Annual Volatility: 12.03%
  Sharpe Ratio: 2.083
  Max Drawdown: -25.59%
  Win Rate: 42.6%

Baseline (100% ACWI):
  Days: 2926
  Final Val

In [9]:
# Create a second plot: Monthly Alpha distribution by N
fig2 = go.Figure()

# Color palette (ensure available for this cell)
colors = {
    'N=3': '#00D9FF',  # Cyan
    'N=4': '#FFD700',  # Gold
    'N=5': '#00FF41',  # Green
    'N=6': '#FF6B6B',  # Red
    'N=7': '#9D4EDD',  # Purple
    'Baseline': '#888888', # Gray
}

for label in sorted(backtest_dfs.keys()):
    df = backtest_dfs[label]
    fig2.add_trace(go.Scatter(
        x=df['date'],
        y=df['avg_alpha'],
        mode='lines+markers',
        name=label,
        line=dict(color=colors.get(label, '#FFFFFF'), width=1.5),
        marker=dict(size=3),
        hovertemplate=f'<b>{label}</b><br>Date: %{{x|%Y-%m-%d}}<br>Monthly Alpha: %{{y:.2%}}<extra></extra>'
    ))

# Add zero line for baseline
if baseline_dates is not None:
    fig2.add_trace(go.Scatter(
        x=baseline_dates,
        y=[0] * len(baseline_dates),
        mode='lines',
        name='Zero (Baseline)',
        line=dict(color=colors['Baseline'], width=2, dash='dash'),
        hovertemplate='<b>Baseline</b><br>Date: %{x|%Y-%m-%d}<br>Alpha: 0.00%<extra></extra>'
    ))

fig2.update_layout(
    title={
        'text': 'Monthly Alpha by Satellite Count (N)',
        'x': 0.5,
        'xanchor': 'center',
        'font': {'size': 20, 'color': '#FFFFFF'}
    },
    xaxis=dict(
        title='Date',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        color='#FFFFFF'
    ),
    yaxis=dict(
        title='Monthly Alpha',
        tickformat='.2%',
        showgrid=True,
        gridwidth=1,
        gridcolor='#333333',
        zeroline=True,
        zerolinecolor='#666666',
        color='#FFFFFF'
    ),
    plot_bgcolor='#1a1a1a',
    paper_bgcolor='#0d0d0d',
    font=dict(color='#FFFFFF', size=12),
    hovermode='x unified',
    legend=dict(
        bgcolor='rgba(0,0,0,0.5)',
        bordercolor='#FFFFFF',
        borderwidth=1,
        font=dict(color='#FFFFFF')
    ),
    height=700,
    width=1400,
    margin=dict(l=80, r=80, t=100, b=80)
)

fig2.show()